# Using volcano plot code (originally for Lians fig) to pull out RNAs and all genes significantly up in 500ppm relative to CH4 limited

In [1]:
import altair as alt
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

from override import GENE_NAME_OVERRIDE, GENE_PRODUCT_OVERRIDE
from Bio import SeqIO


In [2]:
# get feature info from genbank

def get_override_gene(locus_tag,cur_gene):
    '''
    Given a locus tag, return an overridden gene
    '''
    return GENE_NAME_OVERRIDE[locus_tag] if locus_tag in GENE_NAME_OVERRIDE else cur_gene

def get_override_product(locus_tag,cur_prod):
    '''
    Given a locus tag, return an overridden gene
    '''
    return GENE_PRODUCT_OVERRIDE[locus_tag] if locus_tag in GENE_PRODUCT_OVERRIDE else cur_prod

def get_feat2meta_dict(genbank_path):
    '''
    Given a genbank file, parse it and return a dictionary of locus and the 
    gene, product and type fields
    '''
    seq_record = SeqIO.parse(genbank_path, "genbank").__next__()
    feat_list = []
    # Loop over the genome file, get the features on each of the strands
    for feature in seq_record.features:
        if feature.type != 'gene': # exclude 'gene' wrapper type
            if 'locus_tag' in feature.qualifiers: # exclude features without a locus tag
                # get  locus tag, feature name and product
                lt = feature.qualifiers['locus_tag'][0]
                g = "" if 'gene' not in feature.qualifiers else feature.qualifiers['gene'][0]
                prod = "" if 'product' not in feature.qualifiers else feature.qualifiers['product'][0]
                t = feature.type
                strand = feature.strand
                seq = str(feature.location.extract(seq_record).seq)

                # overrides
                g = get_override_gene(lt,g)
                prod = get_override_product(lt,prod)

                metadata = {
                    'gene_symbol':g,
                    'product':prod,
                    'type':t,
                    'strand':strand,
                    'seq':seq
                }

                feat_list.append((lt,metadata))

    return dict(feat_list)

In [3]:
gb_file = "data/5GB1c_sequence_20220411.gb"
loc2info = get_feat2meta_dict(gb_file)

loc2info['EQU24_RS19315']

{'gene_symbol': 'pmoC',
 'product': 'methane monooxygenase/ammonia monooxygenase subunit C',
 'type': 'CDS',
 'strand': -1,
 'seq': 'ATGGCTGCTACAACTGAGTCAGTTAAAGCTGATGCTGCAGAAGCACCACTTTTGAACAAAAAAAATATAATTGCCGGTGCATCTTTGTACCTGGTATTTTATGCTTGGGTTCGTTGGTATGAAGGCGTTTATGGCTGGTCCGCCGGTCTTGACTCTTTCGCTCCGGAATTCGAAACTTACTGGATGAACTTCCTGTACATCGAAATGGTTCTGGAAGTATTGACAGCTTCTATCTTGTGGGGTTATATCTGGAAAACTCGTGATCGTAAAGTGATGTCAATCACTCCACGTGAAGAGTTGAGAAGACATTTTACTCACTGGACATGGCTAATGATGTACGGCATCGCGATCTACTTCGGTGCTAGCTACTTCACAGAGCAAGACGGTACATGGCATCAAACCATCGTACGTGATACTGACTTCACTCCAAGTCATATCATTGAGTTCTACTTGAGCTACCCAATCTATATCATCACTGGTGGCGCTTCTTTCTTGTACGCTAAAACAAGACTTCCAACTTACCAACAAGGTTTGTCTCTGCAATACCTGGTTGTTGTTGTAGGTCCATTCATGATTCTGCCAAACGTTGGTTTGAACGAGTGGGGTCATACTTTCTGGTTTATGGAAGAATTGTTTGTTGCTCCTCTGCACTATGGTTTCGTCTTCTTCGGATGGTCGGCTCTGGGTGTATTGGGTGTAATCAACATCGAGTTGGGCGCATTGTCCAAGCTGCTGAAAAAAGACTTAGCATAA'}

In [23]:
# differential expression files
ch500_df = pd.read_csv('data/exp_condition_CH4_500ppm_vs_lowCH4.tsv',sep='\t')
ch500_df = ch500_df.reset_index().rename(columns={'index':'locus_tag'})
ch500_df['ch4_level'] = '500ppm'
display(ch500_df.head())

ch1000_df = pd.read_csv('data/exp_condition_CH4_1000ppm_vs_lowCH4.tsv',sep='\t')
ch1000_df = ch1000_df.reset_index().rename(columns={'index':'locus_tag'})
ch1000_df['ch4_level'] = '1000ppm'
display(ch1000_df.head())

ch_df = pd.concat([ch500_df,ch1000_df])
ch_df['padj_invlog'] = ch_df['padj'].apply(lambda x: -np.log10(x))
ch_df['abs_log2fc'] = np.abs(ch_df['log2FoldChange'])


ch_df

locus_tag     baseMean  log2FoldChange     lfcSE      stat    pvalue  \
0  EQU24_RS00005   978.904659        0.553172  0.155627  3.554466  0.000379   
1  EQU24_RS00010  1006.377442       -0.350918  0.182868 -1.918965  0.054989   
2  EQU24_RS00015   522.894898        0.120708  0.157373  0.767022  0.443069   
3  EQU24_RS00020  2573.605057       -0.108161  0.145295 -0.744421  0.456622   
4  EQU24_RS00035   574.805889       -0.027342  0.246114 -0.111093  0.911542   

       padj ch4_level  
0  0.001000    500ppm  
1  0.087342    500ppm  
2  0.520830    500ppm  
3  0.534725    500ppm  
4  0.932222    500ppm

locus_tag     baseMean  log2FoldChange     lfcSE      stat    pvalue  \
0  EQU24_RS00005   978.904659        0.067246  0.155342  0.432889  0.665096   
1  EQU24_RS00010  1006.377442       -0.410048  0.182303 -2.249268  0.024495   
2  EQU24_RS00015   522.894898       -0.293357  0.157080 -1.867561  0.061823   
3  EQU24_RS00020  2573.605057        0.079233  0.145007  0.546409  0.584785   
4  EQU24_RS00035   574.805889        0.249371  0.244742  1.018914  0.308244   

       padj ch4_level  
0  0.731059   1000ppm  
1  0.044711   1000ppm  
2  0.099813   1000ppm  
3  0.663224   1000ppm  
4  0.392346   1000ppm

locus_tag      baseMean  log2FoldChange     lfcSE      stat  \
0     EQU24_RS00005    978.904659        0.553172  0.155627  3.554466   
1     EQU24_RS00010   1006.377442       -0.350918  0.182868 -1.918965   
2     EQU24_RS00015    522.894898        0.120708  0.157373  0.767022   
3     EQU24_RS00020   2573.605057       -0.108161  0.145295 -0.744421   
4     EQU24_RS00035    574.805889       -0.027342  0.246114 -0.111093   
...             ...           ...             ...       ...       ...   
4184  EQU24_RS23155  33281.507902        0.040945  0.326197  0.125521   
4185  EQU24_RS23160  21328.143416       -0.103794  0.268584 -0.386447   
4186  EQU24_RS23165  32819.819287       -0.309035  0.320198 -0.965138   
4187  EQU24_RS23170    585.412492       -0.425610  0.271593 -1.567088   
4188  EQU24_RS23175     12.445295       -2.711763  0.290203 -9.344376   

            pvalue          padj ch4_level  padj_invlog  abs_log2fc  
0     3.787481e-04  9.996956e-04    500ppm     3.000132    0.553172  
1     5.498878e-02  8.734158e-02    500ppm     1.058779    0.350918  
2     4.430687e-01  5.208296e-01    500ppm     0.283304    0.120708  
3     4.566221e-01  5.347250e-01    500ppm     0.271870    0.108161  
4     9.115424e-01  9.322223e-01    500ppm     0.030481    0.027342  
...            ...           ...       ...          ...         ...  
4184  9.001111e-01  9.224127e-01   1000ppm     0.035075    0.040945  
4185  6.991656e-01  7.597171e-01   1000ppm     0.119348    0.103794  
4186  3.344759e-01  4.185643e-01   1000ppm     0.378238    0.309035  
4187  1.170942e-01  1.724603e-01   1000ppm     0.763311    0.425610  
4188  9.243268e-21  2.575277e-19   1000ppm    18.589176    2.711763  

[8378 rows x 10 columns]

In [5]:
ch500_df.shape

(4189, 8)

## Collect metadata from TPM df

In [6]:
with open('data/sample2condition.txt','r') as f:
    sample2cond = dict([x.strip().split('\t') for x in f.readlines()])
    samples = list(sample2cond.keys())

In [7]:
# tpm file
tpm_df = pd.read_csv('data/5GB1_tpms_20221031.tsv',sep='\t').fillna("")
tpm_df

locus_tag                                            product type  \
0     EQU24_RS00005     chromosomal replication initiator protein DnaA  CDS   
1     EQU24_RS00010                    DNA polymerase III subunit beta  CDS   
2     EQU24_RS00015                DNA replication/repair protein RecF  CDS   
3     EQU24_RS00020      DNA topoisomerase (ATP-hydrolyzing) subunit B  CDS   
4     EQU24_RS00035                               hypothetical protein  CDS   
...             ...                                                ...  ...   
4184  EQU24_RS23155                    3-hexulose-6-phosphate synthase  CDS   
4185  EQU24_RS23160                        6-phospho-3-hexuloisomerase  CDS   
4186  EQU24_RS23165                    3-hexulose-6-phosphate synthase  CDS   
4187  EQU24_RS23170                                        transposase  CDS   
4188  EQU24_RS23175  type II toxin-antitoxin system RelE/ParE famil...  CDS   

     gene_symbol          locus  start_coord  end_coord  \
0           dnaA  NZ_CP035467.1            0       1317   
1           dnaN  NZ_CP035467.1         1502       2603   
2           recF  NZ_CP035467.1         3060       4140   
3           gyrB  NZ_CP035467.1         4185       6600   
4                 NZ_CP035467.1         7350       7734   
...          ...            ...          ...        ...   
4184        hxlA  NZ_CP035467.1      4877662    4878310   
4185        hxlB  NZ_CP035467.1      4882314    4882848   
4186        hxlA  NZ_CP035467.1      4882851    4883499   
4187              NZ_CP035467.1      4918898    4919603   
4188              NZ_CP035467.1      4919710    4919809   

                                                   note  gene_len  \
0     Derived by automated computational analysis us...      1318   
1     Derived by automated computational analysis us...      1102   
2     Derived by automated computational analysis us...      1081   
3     Derived by automated computational analysis us...      2416   
4     Derived by automated computational analysis us...       385   
...                                                 ...       ...   
4184  Derived by automated computational analysis us...       649   
4185  Derived by automated computational analysis us...       535   
4186  Derived by automated computational analysis us...       649   
4187  Derived by automated computational analysis us...       706   
4188  Derived by automated computational analysis us...       100   

      5GB1_ferm_Ack_QC_tpm  ...  5GB1C-5G-N-BR1_tpm  5GB1C-5G-N-BR2_tpm  \
0                 2.920380  ...           38.638102           31.867873   
1                 1.600865  ...           45.092244           45.889651   
2                 1.409423  ...           21.362765           20.976809   
3                 3.186309  ...           57.478160           61.623220   
4                 8.852007  ...          118.910610          106.287739   
...                    ...  ...                 ...                 ...   
4184             54.488824  ...         4912.583048         5746.455924   
4185             39.120128  ...         2384.223783         2787.974601   
4186             49.546527  ...         4663.779462         5303.775431   
4187              5.792673  ...           36.226783           48.282299   
4188              1.202832  ...            0.162285            0.667332   

      5GB1C-JG15-La-BR1_tpm  5GB1C-JG15-La-BR2_tpm  5GB1C-JG15-N-BR1_tpm  \
0                 30.546267              36.840627             29.198516   
1                 34.824076              44.661748             35.864388   
2                 17.355043              21.854708             18.734014   
3                 52.941842              63.050677             55.592843   
4                102.200487             116.972791            105.924563   
...                     ...                    ...                   ...   
4184            2972.807778            3975.569016           4832.782004   
4185          

In [8]:
# apply gene override names/products
tpm_df['gene_symbol'] = tpm_df['locus_tag'].apply(lambda x: loc2info[x]['gene_symbol'])
tpm_df['product'] = tpm_df['locus_tag'].apply(lambda x: loc2info[x]['product'])
tpm_df[tpm_df['locus_tag']=='EQU24_RS12525']

locus_tag                 product   type gene_symbol locus  \
2285  EQU24_RS12525  transfer-messenger RNA  tmRNA        ssrA         

      start_coord  end_coord note  gene_len  5GB1_ferm_Ack_QC_tpm  ...  \
2285      2807909    2808284            376         364195.629604  ...   

      5GB1C-5G-N-BR1_tpm  5GB1C-5G-N-BR2_tpm  5GB1C-JG15-La-BR1_tpm  \
2285       163378.044864       130870.098679          137852.653857   

      5GB1C-JG15-La-BR2_tpm  5GB1C-JG15-N-BR1_tpm  5GB1C-JG15-N-BR2_tpm  \
2285          178606.335282         178731.713539          81931.066756   

      5GB1C_CH4_500ppm-Rep1_tpm  5GB1C_CH4_500ppm-Rep2_tpm  \
2285              279755.345671              272077.624131   

      5GB1C_CH4_1000ppm-Rep2_tpm  5GB1C_CH4_1000ppm-Rep1_tpm  
2285               213393.339329               272606.270476  

[1 rows x 111 columns]

In [9]:
# drop all sample data cols so we can keep just the few we want
tpm_subdf = tpm_df.drop(samples,axis=1)

# which tpm cols do we actually want around?
cols2keep = ['5GB1C_CH4_500ppm-Rep1_tpm','5GB1C_CH4_500ppm-Rep2_tpm','5GB1C_CH4_1000ppm-Rep1_tpm','5GB1C_CH4_1000ppm-Rep2_tpm']
for col in cols2keep:
    tpm_subdf[col] = tpm_df[col]
tpm_subdf

locus_tag                                            product type  \
0     EQU24_RS00005     chromosomal replication initiator protein DnaA  CDS   
1     EQU24_RS00010                    DNA polymerase III subunit beta  CDS   
2     EQU24_RS00015                DNA replication/repair protein RecF  CDS   
3     EQU24_RS00020      DNA topoisomerase (ATP-hydrolyzing) subunit B  CDS   
4     EQU24_RS00035                               hypothetical protein  CDS   
...             ...                                                ...  ...   
4184  EQU24_RS23155                    3-hexulose-6-phosphate synthase  CDS   
4185  EQU24_RS23160                        6-phospho-3-hexuloisomerase  CDS   
4186  EQU24_RS23165                    3-hexulose-6-phosphate synthase  CDS   
4187  EQU24_RS23170                                        transposase  CDS   
4188  EQU24_RS23175  type II toxin-antitoxin system RelE/ParE famil...  CDS   

     gene_symbol          locus  start_coord  end_coord  \
0           dnaA  NZ_CP035467.1            0       1317   
1           dnaN  NZ_CP035467.1         1502       2603   
2           recF  NZ_CP035467.1         3060       4140   
3           gyrB  NZ_CP035467.1         4185       6600   
4                 NZ_CP035467.1         7350       7734   
...          ...            ...          ...        ...   
4184        hxlA  NZ_CP035467.1      4877662    4878310   
4185        hxlB  NZ_CP035467.1      4882314    4882848   
4186        hxlA  NZ_CP035467.1      4882851    4883499   
4187              NZ_CP035467.1      4918898    4919603   
4188              NZ_CP035467.1      4919710    4919809   

                                                   note  gene_len  \
0     Derived by automated computational analysis us...      1318   
1     Derived by automated computational analysis us...      1102   
2     Derived by automated computational analysis us...      1081   
3     Derived by automated computational analysis us...      2416   
4     Derived by automated computational analysis us...       385   
...                                                 ...       ...   
4184  Derived by automated computational analysis us...       649   
4185  Derived by automated computational analysis us...       535   
4186  Derived by automated computational analysis us...       649   
4187  Derived by automated computational analysis us...       706   
4188  Derived by automated computational analysis us...       100   

      5GB1C_CH4_500ppm-Rep1_tpm  5GB1C_CH4_500ppm-Rep2_tpm  \
0                     56.747208                  55.734395   
1                     32.721559                  33.467532   
2                     26.409599                  23.529439   
3                     48.167231                  51.249206   
4                     86.942252                  83.059104   
...                         ...                        ...   
4184                2093.320771                2189.062660   
4185                1521.529928                1598.613630   
4186                1613.939517                1649.074688   
4187                  32.119364                  25.035217   
4188                   1.140292                   0.985171   

      5GB1C_CH4_1000ppm-Rep1_tpm  5GB1C_CH4_1000ppm-Rep2_tpm  
0                      35.325741                   46.812595  
1                      30.020538                   34.906928  
2                      16.896055                   21.368579  
3                      54.226180                   61.811500  
4                      94.451247                  118.967455  
...                          ...                         ...  
4184                 2556.194919                 2612.122268  
4185                 1962.755769                 2081.876627  
4186                 1940.573398                 2003.711339  
4187                   26.694263                   28.898838  
4188                    0.594248                    0.880882  

[4189 rows x 13 colum

In [10]:
tpm_subdf[cols2keep[:2]]

5GB1C_CH4_500ppm-Rep1_tpm  5GB1C_CH4_500ppm-Rep2_tpm
0                     56.747208                  55.734395
1                     32.721559                  33.467532
2                     26.409599                  23.529439
3                     48.167231                  51.249206
4                     86.942252                  83.059104
...                         ...                        ...
4184                2093.320771                2189.062660
4185                1521.529928                1598.613630
4186                1613.939517                1649.074688
4187                  32.119364                  25.035217
4188                   1.140292                   0.985171

[4189 rows x 2 columns]

In [32]:
tpm_subdf['mean500_tpm'] = tpm_subdf[cols2keep[:2]].mean(axis=1)
tpm_subdf['mean1000_tpm'] = tpm_subdf[cols2keep[2:]].mean(axis=1)
tpm_subdf['mean_tpm'] = tpm_subdf[cols2keep].mean(axis=1)
tpm_subdf['log2_mean_tpm'] = np.log2(tpm_subdf['mean_tpm'])
tpm_subdf

locus_tag                                            product type  \
0     EQU24_RS00005     chromosomal replication initiator protein DnaA  CDS   
1     EQU24_RS00010                    DNA polymerase III subunit beta  CDS   
2     EQU24_RS00015                DNA replication/repair protein RecF  CDS   
3     EQU24_RS00020      DNA topoisomerase (ATP-hydrolyzing) subunit B  CDS   
4     EQU24_RS00035                               hypothetical protein  CDS   
...             ...                                                ...  ...   
4184  EQU24_RS23155                    3-hexulose-6-phosphate synthase  CDS   
4185  EQU24_RS23160                        6-phospho-3-hexuloisomerase  CDS   
4186  EQU24_RS23165                    3-hexulose-6-phosphate synthase  CDS   
4187  EQU24_RS23170                                        transposase  CDS   
4188  EQU24_RS23175  type II toxin-antitoxin system RelE/ParE famil...  CDS   

     gene_symbol          locus  start_coord  end_coord  \
0           dnaA  NZ_CP035467.1            0       1317   
1           dnaN  NZ_CP035467.1         1502       2603   
2           recF  NZ_CP035467.1         3060       4140   
3           gyrB  NZ_CP035467.1         4185       6600   
4                 NZ_CP035467.1         7350       7734   
...          ...            ...          ...        ...   
4184        hxlA  NZ_CP035467.1      4877662    4878310   
4185        hxlB  NZ_CP035467.1      4882314    4882848   
4186        hxlA  NZ_CP035467.1      4882851    4883499   
4187              NZ_CP035467.1      4918898    4919603   
4188              NZ_CP035467.1      4919710    4919809   

                                                   note  gene_len  \
0     Derived by automated computational analysis us...      1318   
1     Derived by automated computational analysis us...      1102   
2     Derived by automated computational analysis us...      1081   
3     Derived by automated computational analysis us...      2416   
4     Derived by automated computational analysis us...       385   
...                                                 ...       ...   
4184  Derived by automated computational analysis us...       649   
4185  Derived by automated computational analysis us...       535   
4186  Derived by automated computational analysis us...       649   
4187  Derived by automated computational analysis us...       706   
4188  Derived by automated computational analysis us...       100   

      5GB1C_CH4_500ppm-Rep1_tpm  5GB1C_CH4_500ppm-Rep2_tpm  \
0                     56.747208                  55.734395   
1                     32.721559                  33.467532   
2                     26.409599                  23.529439   
3                     48.167231                  51.249206   
4                     86.942252                  83.059104   
...                         ...                        ...   
4184                2093.320771                2189.062660   
4185                1521.529928                1598.613630   
4186                1613.939517                1649.074688   
4187                  32.119364                  25.035217   
4188                   1.140292                   0.985171   

      5GB1C_CH4_1000ppm-Rep1_tpm  5GB1C_CH4_1000ppm-Rep2_tpm  mean500_tpm  \
0                      35.325741                   46.812595    56.240801   
1                      30.020538                   34.906928    33.094545   
2                      16.896055                   21.368579    24.969519   
3                      54.226180                   61.811500    49.708219   
4                      94.451247                  118.967455    85.000678   
...                          ...                         ...          ...   
4184                 2556.194919                 2612.122268  2141.191715   
4185                 1962.755769                 2081.876627  1560.071779   
4186                 1940.573398                 2003.711339  1631.507103   
4187    

In [33]:
# merge this in with the deseqdf
df = pd.merge(ch_df, tpm_subdf,how='left',on='locus_tag')
df

locus_tag      baseMean  log2FoldChange     lfcSE      stat  \
0     EQU24_RS00005    978.904659        0.553172  0.155627  3.554466   
1     EQU24_RS00010   1006.377442       -0.350918  0.182868 -1.918965   
2     EQU24_RS00015    522.894898        0.120708  0.157373  0.767022   
3     EQU24_RS00020   2573.605057       -0.108161  0.145295 -0.744421   
4     EQU24_RS00035    574.805889       -0.027342  0.246114 -0.111093   
...             ...           ...             ...       ...       ...   
8373  EQU24_RS23155  33281.507902        0.040945  0.326197  0.125521   
8374  EQU24_RS23160  21328.143416       -0.103794  0.268584 -0.386447   
8375  EQU24_RS23165  32819.819287       -0.309035  0.320198 -0.965138   
8376  EQU24_RS23170    585.412492       -0.425610  0.271593 -1.567088   
8377  EQU24_RS23175     12.445295       -2.711763  0.290203 -9.344376   

            pvalue          padj ch4_level  padj_invlog  abs_log2fc  ...  \
0     3.787481e-04  9.996956e-04    500ppm     3.000132    0.553172  ...   
1     5.498878e-02  8.734158e-02    500ppm     1.058779    0.350918  ...   
2     4.430687e-01  5.208296e-01    500ppm     0.283304    0.120708  ...   
3     4.566221e-01  5.347250e-01    500ppm     0.271870    0.108161  ...   
4     9.115424e-01  9.322223e-01    500ppm     0.030481    0.027342  ...   
...            ...           ...       ...          ...         ...  ...   
8373  9.001111e-01  9.224127e-01   1000ppm     0.035075    0.040945  ...   
8374  6.991656e-01  7.597171e-01   1000ppm     0.119348    0.103794  ...   
8375  3.344759e-01  4.185643e-01   1000ppm     0.378238    0.309035  ...   
8376  1.170942e-01  1.724603e-01   1000ppm     0.763311    0.425610  ...   
8377  9.243268e-21  2.575277e-19   1000ppm    18.589176    2.711763  ...   

                                                   note gene_len  \
0     Derived by automated computational analysis us...     1318   
1     Derived by automated computational analysis us...     1102   
2     Derived by automated computational analysis us...     1081   
3     Derived by automated computational analysis us...     2416   
4     Derived by automated computational analysis us...      385   
...                                                 ...      ...   
8373  Derived by automated computational analysis us...      649   
8374  Derived by automated computational analysis us...      535   
8375  Derived by automated computational analysis us...      649   
8376  Derived by automated computational analysis us...      706   
8377  Derived by automated computational analysis us...      100   

     5GB1C_CH4_500ppm-Rep1_tpm 5GB1C_CH4_500ppm-Rep2_tpm  \
0                    56.747208                 55.734395   
1                    32.721559                 33.467532   
2                    26.409599                 23.529439   
3                    48.167231                 51.249206   
4                    86.942252                 83.059104   
...                        ...                       ...   
8373               2093.320771               2189.062660   
8374               1521.529928               1598.613630   
8375               1613.939517               1649.074688   
8376                 32.119364                 25.035217   
8377                  1.140292                  0.985171   

      5GB1C_CH4_1000ppm-Rep1_tpm  5GB1C_CH4_1000ppm-Rep2_tpm  mean500_tpm  \
0                      35.325741                   46.812595    56.240801   
1                      30.020538                   34.906928    33.094545   
2                      16.896055                   21.368579    24.969519   
3                      54.226180                   61.811500    49.708219   
4                      94.451247                  118.967455    85.000678   
...                          ...                         ...          ...   
8373                 2556.194919                 2612.122268  2141.191715   
8374                 1962.755769                 2081.876627  1560

In [34]:
df.columns

Index(['locus_tag', 'baseMean', 'log2FoldChange', 'lfcSE', 'stat', 'pvalue',
       'padj', 'ch4_level', 'padj_invlog', 'abs_log2fc', 'product', 'type',
       'gene_symbol', 'locus', 'start_coord', 'end_coord', 'note', 'gene_len',
       '5GB1C_CH4_500ppm-Rep1_tpm', '5GB1C_CH4_500ppm-Rep2_tpm',
       '5GB1C_CH4_1000ppm-Rep1_tpm', '5GB1C_CH4_1000ppm-Rep2_tpm',
       'mean500_tpm', 'mean1000_tpm', 'mean_tpm', 'log2_mean_tpm'],
      dtype='object')

## Volcano plots

In [35]:
# remove CDS
#df = df[df['type']!='CDS']
df.shape

(8378, 26)

In [36]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [37]:
def is_sig(pval, fc, pthresh=0.05,fc_thresh=1):
    if pval<pthresh and np.abs(fc) > fc_thresh:
        return True
    else:
        return False

In [38]:
df['is_sig'] = df.apply(lambda row: is_sig(row['padj'],row['log2FoldChange']),axis=1)

In [39]:
df[df['is_sig']==True]

locus_tag      baseMean  log2FoldChange     lfcSE       stat  \
5     EQU24_RS00040    596.371349       -1.216696  0.173530  -7.011435   
8     EQU24_RS00055     89.081753       -1.032225  0.190369  -5.422246   
16    EQU24_RS00100    648.422350       -1.563394  0.192056  -8.140287   
17    EQU24_RS00105   1478.557057       -2.926870  0.245128 -11.940193   
18    EQU24_RS00110   1558.965687       -1.741020  0.269220  -6.466904   
...             ...           ...             ...       ...        ...   
8352  EQU24_RS23020    153.502802       -1.925443  0.244455  -7.876473   
8354  EQU24_RS23035     77.704041       -1.420281  0.209651  -6.774514   
8361  EQU24_RS23090  24975.366114        1.666209  0.381665   4.365633   
8364  EQU24_RS23110     46.086638        2.197052  0.220487   9.964546   
8377  EQU24_RS23175     12.445295       -2.711763  0.290203  -9.344376   

            pvalue          padj ch4_level  padj_invlog  abs_log2fc  ...  \
5     2.358867e-12  2.426609e-11    500ppm    10.615000    1.216696  ...   
8     5.885495e-08  3.160991e-07    500ppm     6.500177    1.032225  ...   
16    3.943415e-16  6.484008e-15    500ppm    14.188156    1.563394  ...   
17    7.305381e-33  4.804785e-31    500ppm    30.318326    2.926870  ...   
18    1.000310e-10  8.520687e-10    500ppm     9.069525    1.741020  ...   
...            ...           ...       ...          ...         ...  ...   
8352  3.367529e-15  5.425914e-14   1000ppm    13.265527    1.925443  ...   
8354  1.248254e-11  1.349864e-10   1000ppm     9.869710    1.420281  ...   
8361  1.267552e-05  5.060116e-05   1000ppm     4.295840    1.666209  ...   
8364  2.178673e-23  7.407489e-22   1000ppm    21.130329    2.197052  ...   
8377  9.243268e-21  2.575277e-19   1000ppm    18.589176    2.711763  ...   

     gene_len 5GB1C_CH4_500ppm-Rep1_tpm 5GB1C_CH4_500ppm-Rep2_tpm  \
5        1258                  9.987241                  9.881611   
8         307                  8.239010                  6.476398   
16        481                 33.480332                 25.937312   
17        655                 17.329913                 15.280064   
18        418                 48.557909                 47.330203   
...       ...                       ...                       ...   
8352      766                  2.287081                  2.782705   
8354      361                  3.546364                  4.105913   
8361      706               4404.955975               4998.436203   
8364       91                104.574274                 98.812356   
8377      100                  1.140292                  0.985171   

     5GB1C_CH4_1000ppm-Rep1_tpm  5GB1C_CH4_1000ppm-Rep2_tpm  mean500_tpm  \
5                     10.456362                   11.249369     9.934426   
8                      8.904041                    9.810874     7.357704   
16                    29.606503                   29.935615    29.708822   
17                    16.220312                   19.112499    16.304989   
18                    52.154092                   60.465393    47.944056   
...                         ...                         ...          ...   
8352                   2.028112                    2.640523     2.534893   
8354                   2.986525                    3.697714     3.826139   
8361                4604.189138                 5654.632090  4701.696089   
8364                  82.140553                  106.778075   101.693315   
8377                   0.594248                    0.880882     1.062732   

     mean1000_tpm     mean_tpm  log2_mean_tpm  is_sig  
5       10.852865    10.393646       3.377630    True  
8        9.357458     8.357581       3.063085    True  
16      29.771059    29.739940       4.894330    True  
17      17.666406    16.985697       4.086249    True  
18      56.309743    52.126899       5.703956    True  
...           ...          ...            ...     ...  
8352     2.334317     2.434605       1.283688    True  
8354     3.342120 

In [40]:
# significance thresholds
thresh_low = alt.Chart(pd.DataFrame({'x': [-1]})).mark_rule(strokeDash=[12, 6],size=2).encode(x='x')
thresh_high = alt.Chart(pd.DataFrame({'x': [1]})).mark_rule(strokeDash=[12, 6],size=2).encode(x='x')
sig_p = 0.05
thresh_sig = alt.Chart(pd.DataFrame({'y': [-np.log10(sig_p)]})).mark_rule(strokeDash=[12, 6],size=2).encode(y='y')

bubble_max = 300

In [41]:
def volcano_all_data(df,filename='alt_out/volcano_rna.html',plot_title=False):
    points = alt.Chart(df).mark_point().encode(
        x=alt.X('log2FoldChange:Q',title="log\u2082 Fold Change"),
        y=alt.Y('padj_invlog:Q', title="-log\u2081\u2080 p-value",
                axis=alt.Axis(tickCount=3)),
        color = alt.condition(alt.datum.is_sig,
                       alt.Color('ch4_level:N',
                                 title='CH\u2084 Level',
                                 scale=alt.Scale(domain=['500ppm', '1000ppm'], range=['#1f78b4', '#d95f02'])),
                       alt.value('lightgray')
        ),
        size=alt.Size('mean_tpm:Q',
                      title='Mean TPM',
                      scale=alt.Scale(domain=[1, 100000], range=[1, bubble_max],type='log')),
        tooltip=['locus_tag:N','gene_symbol:N', 'product:N',
                 alt.Tooltip('mean500_tpm:Q',format='.2f'),
                 alt.Tooltip('mean1000_tpm:Q',format='.2f')],
    ).properties(
        title=f"{'All data' if plot_title else ''}",
    ).interactive()

    chart = points + thresh_low + thresh_high + thresh_sig

#     chart = chart.configure_axis(
#         grid=False,
#         titleFontSize=20,
#         labelFontSize=14
#     )
    
    chart.save(filename)
    return chart

In [42]:
v_all = volcano_all_data(df)
v_all

alt.LayerChart(...)

In [46]:
df.columns


Index(['locus_tag', 'baseMean', 'log2FoldChange', 'lfcSE', 'stat', 'pvalue',
       'padj', 'ch4_level', 'padj_invlog', 'abs_log2fc', 'product', 'type',
       'gene_symbol', 'locus', 'start_coord', 'end_coord', 'note', 'gene_len',
       '5GB1C_CH4_500ppm-Rep1_tpm', '5GB1C_CH4_500ppm-Rep2_tpm',
       '5GB1C_CH4_1000ppm-Rep1_tpm', '5GB1C_CH4_1000ppm-Rep2_tpm',
       'mean500_tpm', 'mean1000_tpm', 'mean_tpm', 'log2_mean_tpm', 'is_sig'],
      dtype='object')

In [47]:
cols = ['locus_tag','product','gene_symbol','ch4_level','type','mean500_tpm','mean1000_tpm']
deseq_cols = ['baseMean', 'log2FoldChange', 'lfcSE', 'stat', 'pvalue','padj','padj_invlog', 'abs_log2fc']
df[cols]

locus_tag                                            product  \
0     EQU24_RS00005     chromosomal replication initiator protein DnaA   
1     EQU24_RS00010                    DNA polymerase III subunit beta   
2     EQU24_RS00015                DNA replication/repair protein RecF   
3     EQU24_RS00020      DNA topoisomerase (ATP-hydrolyzing) subunit B   
4     EQU24_RS00035                               hypothetical protein   
...             ...                                                ...   
8373  EQU24_RS23155                    3-hexulose-6-phosphate synthase   
8374  EQU24_RS23160                        6-phospho-3-hexuloisomerase   
8375  EQU24_RS23165                    3-hexulose-6-phosphate synthase   
8376  EQU24_RS23170                                        transposase   
8377  EQU24_RS23175  type II toxin-antitoxin system RelE/ParE famil...   

     gene_symbol ch4_level type  mean500_tpm  mean1000_tpm  
0           dnaA    500ppm  CDS    56.240801     41.069168  
1           dnaN    500ppm  CDS    33.094545     32.463733  
2           recF    500ppm  CDS    24.969519     19.132317  
3           gyrB    500ppm  CDS    49.708219     58.018840  
4                   500ppm  CDS    85.000678    106.709351  
...          ...       ...  ...          ...           ...  
8373        hxlA   1000ppm  CDS  2141.191715   2584.158594  
8374        hxlB   1000ppm  CDS  1560.071779   2022.316198  
8375        hxlA   1000ppm  CDS  1631.507103   1972.142368  
8376               1000ppm  CDS    28.577290     27.796550  
8377               1000ppm  CDS     1.062732      0.737565  

[8378 rows x 7 columns]

In [56]:
rna_up = df[(df['is_sig']==True) & 
            (df['log2FoldChange']>1) & 
            (df['type']!='CDS')][cols+deseq_cols].sort_values('log2FoldChange',ascending=False)
rna_up = rna_up[rna_up['ch4_level']=='500ppm']
rna_up

locus_tag                                      product gene_symbol  \
3079  EQU24_RS16875                                     tRNA-Arg               
1763  EQU24_RS09685                                     tRNA-Ser               
254   EQU24_RS01370                                     tRNA-Thr               
1682  EQU24_RS09235  signal recognition particle sRNA small type         ffs   
385   EQU24_RS02110                                     tRNA-Arg               
1164  EQU24_RS06320                                     tRNA-Leu               

     ch4_level   type  mean500_tpm  mean1000_tpm    baseMean  log2FoldChange  \
3079    500ppm   tRNA  4181.204939   2648.383427  478.030596        4.863896   
1763    500ppm   tRNA  1241.700264   1015.368590  497.369928        2.700591   
254     500ppm   tRNA   297.200670    168.469692   64.699786        2.699290   
1682    500ppm  ncRNA  1521.399030   1065.430291  967.764439        1.797797   
385     500ppm   tRNA    71.998587     56.858048   58.210131        1.354243   
1164    500ppm   tRNA   210.201061    202.690839  224.823873        1.173607   

         lfcSE       stat        pvalue          padj  padj_invlog  abs_log2fc  
3079  0.240175  20.251430  3.450782e-91  6.922268e-88    87.159752    4.863896  
1763  0.362252   7.455009  8.986167e-14  1.116177e-12    11.952267    2.700591  
254   0.246420  10.953999  6.357709e-28  2.898537e-26    25.537821    2.699290  
1682  0.472966   3.801113  1.440477e-04  4.136859e-04     3.383329    1.797797  
385   0.375620   3.605358  3.117229e-04  8.359842e-04     3.077802    1.354243  
1164  0.320213   3.665081  2.472604e-04  6.789930e-04     3.168135    1.173607

In [57]:
set(rna_up['locus_tag'].values)

{'EQU24_RS01370',
 'EQU24_RS02110',
 'EQU24_RS06320',
 'EQU24_RS09235',
 'EQU24_RS09685',
 'EQU24_RS16875'}

^^these are the rna loci that are up in 500/1000ppm relative to low CH4

In [63]:
rna_up.to_csv('data/rna_up_deseq_500ppm_to_limCH4.tsv',sep='\t',index=False)

In [50]:
df[df['locus_tag']=='EQU24_RS09235']

locus_tag    baseMean  log2FoldChange     lfcSE      stat    pvalue  \
1682  EQU24_RS09235  967.764439        1.797797  0.472966  3.801113  0.000144   
5871  EQU24_RS09235  967.764439        1.315535  0.461778  2.848850  0.004388   

          padj ch4_level  padj_invlog  abs_log2fc  ... gene_len  \
1682  0.000414    500ppm     3.383329    1.797797  ...       98   
5871  0.009834   1000ppm     2.007249    1.315535  ...       98   

     5GB1C_CH4_500ppm-Rep1_tpm 5GB1C_CH4_500ppm-Rep2_tpm  \
1682               1577.104876               1465.693183   
5871               1577.104876               1465.693183   

     5GB1C_CH4_1000ppm-Rep1_tpm  5GB1C_CH4_1000ppm-Rep2_tpm  mean500_tpm  \
1682                 886.044489                 1244.816093   1521.39903   
5871                 886.044489                 1244.816093   1521.39903   

     mean1000_tpm    mean_tpm  log2_mean_tpm  is_sig  
1682  1065.430291  1293.41466      10.336969    True  
5871  1065.430291  1293.41466      10.336969    True  

[2 rows x 27 columns]

### All loci up

In [61]:
all_up = df[(df['is_sig']==True) &
            (df['log2FoldChange']>1)][cols+deseq_cols].sort_values('log2FoldChange',ascending=False)
all_up = all_up[all_up['ch4_level']=='500ppm']
all_up

locus_tag                                     product gene_symbol  \
1373  EQU24_RS07485                     IS66 family transposase               
3079  EQU24_RS16875                                    tRNA-Arg               
2927  EQU24_RS16055                          cold-shock protein               
4093  EQU24_RS22495                        hypothetical protein               
2003  EQU24_RS10990                        hypothetical protein               
...             ...                                         ...         ...   
3458  EQU24_RS18950                 M20 family metallopeptidase               
1144  EQU24_RS06215                         YbgA family protein               
2656  EQU24_RS14555                         CsbD family protein               
3208  EQU24_RS17600  4Fe-4S dicluster domain-containing protein               
1511  EQU24_RS08270       cytochrome c oxidase assembly protein               

     ch4_level  type   mean500_tpm  mean1000_tpm     baseMean  log2FoldChange  \
1373    500ppm   CDS      1.273558      1.285076     2.562689        5.981902   
3079    500ppm  tRNA   4181.204939   2648.383427   478.030596        4.863896   
2927    500ppm   CDS  16652.755639   8159.981527  4105.037648        4.479315   
4093    500ppm   CDS     78.321211     87.123484    38.145985        4.371356   
2003    500ppm   CDS   1328.262802   1137.728507  1238.748836        3.995720   
...        ...   ...           ...           ...          ...             ...   
3458    500ppm   CDS     46.642810     45.055894   565.380495        1.012126   
1144    500ppm   CDS     42.084642     40.390529   378.613970        1.009806   
2656    500ppm   CDS     10.427429      8.822340    29.532183        1.007452   
3208    500ppm   CDS     58.783825     57.790302   310.683928        1.006703   
1511    500ppm   CDS     39.566291     39.547355   370.611866        1.002673   

         lfcSE       stat        pvalue          padj  padj_invlog  abs_log2fc  
1373  0.416748  14.353753  1.009242e-46  2.024539e-44    43.693674    5.981902  
3079  0.240175  20.251430  3.450782e-91  6.922268e-88    87.159752    4.863896  
2927  0.337755  13.262032  3.843367e-40  4.818621e-38    37.317077    4.479315  
4093  0.360414  12.128691  7.442986e-34  5.238817e-32    31.280767    4.371356  
2003  0.408722   9.776133  1.425538e-22  3.999482e-21    20.397996    3.995720  
...        ...        ...           ...           ...          ...         ...  
3458  0.142598   7.097778  1.267790e-12  1.356367e-11    10.867623    1.012126  
1144  0.302737   3.335588  8.511929e-04  2.089955e-03     2.679863    1.009806  
2656  0.280505   3.591570  3.286919e-04  8.777398e-04     3.056634    1.007452  
3208  0.174594   5.765963  8.119285e-09  5.050321e-08     7.296681    1.006703  
1511  0.214571   4.672927  2.969369e-06  1.187747e-05     4.925276    1.002673  

[428 rows x 15 columns]

In [62]:
all_up.to_csv('data/all_up_deseq_500ppm_to_limCH4.tsv',sep='\t',index=False)

In [39]:
df.columns


Index(['locus_tag', 'baseMean', 'log2FoldChange', 'lfcSE', 'stat', 'pvalue',
       'padj', 'ch4_level', 'padj_invlog', 'abs_log2fc', 'product', 'type',
       'gene_symbol', 'locus', 'start_coord', 'end_coord', 'note', 'gene_len',
       '5GB1C_CH4_500ppm-Rep1_tpm', '5GB1C_CH4_500ppm-Rep2_tpm',
       '5GB1C_CH4_1000ppm-Rep1_tpm', '5GB1C_CH4_1000ppm-Rep2_tpm',
       'mean500_tpm', 'mean1000_tpm', 'mean_tpm', 'log2_mean_tpm', 'is_sig'],
      dtype='object')